In [15]:
import os
from collections import defaultdict
from fuzzywuzzy import fuzz
import re
import pandas as pd

In [16]:
# List of reviewers
reviewers = [
    'achoreviews',
    'aftersound',
    'animagus',
    'arn',
    'bedrock',
    'bryaudioreviews',
    'cammyfi',
    'soundjedi',
    'eplv',
    'timmyv',
    'harpo',
    'hbb',
    'cqtek',
    'hobbytalk',
    'ianfann',
    'iemworld',
    'jacstone',
    'kr0mka',
    'kurin',
    'melatonin',
    'nymz', 
    'pw',
    'recode',
    'rg',
    'shortbus',
    'suporsalad',
    'tgx78',
    'vortexreviews',
    'vsg',
    'wdym',
    'akros',
    'data_mrs'
]

In [17]:
def remove_channel_suffix(file_name):
    file_name = file_name.lower()
    file_name = re.sub(r'\(.*?\)', '', file_name)  # Remove content in brackets
    file_name = file_name.strip()  # Remove leading and trailing spaces

    if " l.csv" in file_name:
        file_name = file_name.replace(" l.csv", ".csv")
    elif " r.csv" in file_name:
        file_name = file_name.replace(" r.csv", ".csv")

    return file_name.strip()  # Remove any extra spaces after channel suffix removal

In [18]:
def group_files_by_iem(files, threshold=100):
    groups = defaultdict(list)
    added_files = set()

    # Create a special "target" group
    target_group = "target"

    for file1 in files:
        modified_file1 = remove_channel_suffix(file1)

        # Check if the file name contains "target"
        if "target" in file1.lower():
            if file1 not in added_files:
                groups[target_group].append(file1)
                added_files.add(file1)
            continue

        if file1 not in added_files:
            groups[file1].append(file1)
            added_files.add(file1)

        for file2 in files:
            if file2 not in added_files:
                modified_file2 = remove_channel_suffix(file2)
                similarity = fuzz.token_set_ratio(modified_file1, modified_file2)

                # If the similarity score is above the threshold, add the file to the group
                if similarity >= threshold:
                    groups[file1].append(file2)
                    added_files.add(file2)
                # If the similarity score is between 95 and the threshold, compare only the IEM part
                elif 99 <= similarity < threshold:
                    iem1 = re.sub(r'[^a-zA-Z0-9]', '', modified_file1.split()[1]) if len(modified_file1.split()) > 1 else ''
                    iem2 = re.sub(r'[^a-zA-Z0-9]', '', modified_file2.split()[1]) if len(modified_file2.split()) > 1 else ''
                    iem_similarity = fuzz.token_set_ratio(iem1, iem2)
                    
                    if iem_similarity >= threshold:
                        groups[file1].append(file2)
                        added_files.add(file2)

    return groups

In [19]:
# Gather all file names
all_files = []

In [20]:
for reviewer in reviewers:
    reviewer_path = f'output/csv/{reviewer}'

    if os.path.exists(reviewer_path):
        files = os.listdir(reviewer_path)
        all_files.extend([(reviewer, file) for file in files])

In [21]:
# Group files by IEM
grouped_files = group_files_by_iem([file for _, file in all_files])

In [22]:
print(f"Total number of files: {len(all_files)}")
print(f"Total number of groups: {len(grouped_files)}")
print(f"Total number of files in groups: {sum([len(files) for files in grouped_files.values()])}")
print(f"Total number of files not in groups: {len(all_files) - sum([len(files) for files in grouped_files.values()])}")
print(f"\nAvg number of files per group: {sum([len(files) for files in grouped_files.values()]) / len(grouped_files)}")

Total number of files: 9882
Total number of groups: 2356
Total number of files in groups: 7668
Total number of files not in groups: 2214

Avg number of files per group: 3.2546689303904923


In [23]:
# Print grouped files
for representative, files in grouped_files.items():
    print(f"{representative}:")
    for file in files:
        reviewers_with_file = [reviewer for reviewer, f in all_files if f == file]
        print(f"  {file} - {', '.join(reviewers_with_file)}")
    print()

7Hz Dioko L.csv:
  7Hz Dioko L.csv - achoreviews, bedrock, timmyv, iemworld, data_mrs
  7HZ SALNOTES DIOKO L.csv - aftersound
  7HZ SALNOTES DIOKO R.csv - aftersound
  7Hz Salnotes Dioko L.csv - arn, pw
  7Hz Dioko R.csv - bedrock, timmyv, hbb, iemworld, data_mrs
  7hz Dioko L.csv - hobbytalk
  7hz Dioko R.csv - hobbytalk
  7HZ DIOKO (bass mod) L.csv - ianfann
  7HZ DIOKO (bass mod) R.csv - ianfann
  7HZ DIOKO L.csv - ianfann
  7HZ DIOKO R.csv - ianfann
  Dioko L.csv - kr0mka
  Dioko R.csv - kr0mka
  Resolve 7Hz Salnotes Dioko Gras L.csv - kurin
  7hz Salnotes Dioko L.csv - nymz
  7hz Salnotes Dioko R.csv - nymz
  7Hz Salnotes Dioko R.csv - pw
  7Hz Salnotes Dioko TapedVent L.csv - pw
  7hz x Crinacle Dioko L.csv - vortexreviews
  7hz x Crinacle Dioko R.csv - vortexreviews
  7hz x Crinacle Dioko Updated L.csv - vortexreviews
  7hz x Crinacle Dioko Updated R.csv - vortexreviews
  7Hz x Crinacle Salnotes Dioko L.csv - vsg
  7Hz x Crinacle Salnotes Dioko R.csv - vsg
  7Hz Dioko (post-op) 

### Dataframe

In [24]:
# ... (previous code remains unchanged)

# Prepare the data for the DataFrame
iem_data = defaultdict(lambda: defaultdict(list))

for representative, files in grouped_files.items():
    for file in files:
        reviewers_with_file = [reviewer for reviewer, f in all_files if f == file]
        for reviewer in reviewers_with_file:
            iem_data[representative][reviewer].append(file)

# Convert the nested dictionary to a pandas DataFrame
iem_df = pd.DataFrame.from_dict(iem_data, orient='index')

# Fill empty cells with an empty list
iem_df = iem_df.applymap(lambda x: x if isinstance(x, list) else [])


In [25]:
iem_df

achoreviews  \
7Hz Dioko L.csv                                        [7Hz Dioko L.csv]   
7Hz Eternal L.csv                                    [7Hz Eternal L.csv]   
7Hz Legato L.csv                                      [7Hz Legato L.csv]   
7Hz Timeless L.csv                                  [7Hz Timeless L.csv]   
7Hz Zero L.csv                                          [7Hz Zero L.csv]   
...                                                                  ...   
710 Btnc (Active, ANC off) L.csv                                      []   
Elegia (Stock Pads) L.csv                                             []   
Elex (Dekoni Elite Fenestrated Sheepskin Pads) ...                    []   
Ola L.csv                                                             []   
test L.csv                                                            []   

                                                                                   bedrock  \
7Hz Dioko L.csv                                         [7Hz Dioko L.csv, 7Hz Dioko R.csv]   
7Hz Eternal L.csv                                   [7Hz Eternal L.csv, 7Hz Eternal R.csv]   
7Hz Legato L.csv                                                                        []   
7Hz Timeless L.csv                                                                      []   
7Hz Zero L.csv                                            [7Hz Zero L.csv, 7Hz Zero R.csv]   
...                                                                                    ...   
710 Btnc (Active, ANC off) L.csv                                                        []   
Elegia (Stock Pads) L.csv                                                               []   
Elex (Dekoni Elite Fenestrated Sheepskin Pads) ...                                      []   
Ola L.csv                                                                               []   
test L.csv                                                                              []   

                                                                                               timmyv  \
7Hz Dioko L.csv                                                    [7Hz Dioko L.csv, 7Hz Dioko R.csv]   
7Hz Eternal L.csv                                                                                  []   
7Hz Legato L.csv                                                 [7Hz Legato L.csv, 7Hz Legato R.csv]   
7Hz Timeless L.csv                                  [7Hz Timeless L.csv, 7Hz Timeless R.csv, 7Hz T...   
7Hz Zero L.csv                                                       [7Hz Zero L.csv, 7Hz Zero R.csv]   
...                                                                                               ...   
710 Btnc (Active, ANC off) L.csv                                                                   []   
Elegia (Stock Pads) L.csv                                                                          []   
Elex (Dekoni Elite Fenestrated Sheepskin Pads) ...                                                 []   
Ola L.csv                                                                                          []   
test L.csv                                                                                         []   

                                                                                             iemworld  \
7Hz Dioko L.csv                                                    [7Hz Dioko L.csv, 7Hz Dioko R.csv]   
7Hz Eternal L.csv                                              [7Hz ETERNAL L.csv, 7Hz ETERNAL R.csv]   
7Hz Legato L.csv                                                                                   []   
7Hz Timeless L.csv                                  [7Hz Timeless (FINAL Tips) L.csv, 7Hz Timeless...   
7Hz Zero L.csv                                      [7hz Zero (EJ07 FOAM Eartips) L.csv, 7hz Zero ...   
...                                                                                               ...   
710 Btnc (Active, ANC o

### Average

In [41]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.interpolate import interp1d
from scipy.signal import savgol_filter

def calculate_average(data_frames, x_values):

    def interpolate_and_restore_nans(y_values, window):
        not_nan = ~np.isnan(y_values)
        indices = np.arange(len(y_values))
        interpolated_y_values = np.interp(indices, indices[not_nan], y_values[not_nan])
        filtered_y_values = savgol_filter(interpolated_y_values, window, 3)
        filtered_y_values[~not_nan] = np.nan
        return filtered_y_values

    # Interpolate all DataFrames to common x_values
    data = []
    for df in data_frames:
        min_x = df['X'].min()
        max_x = df['X'].max()
        x_values_interp = x_values[(x_values >= min_x) & (x_values <= max_x)]
        f = interp1d(df['X'], df['Y'], kind='linear', fill_value='extrapolate')
        y_values = np.empty_like(x_values)
        y_values[:] = np.nan
        y_values[(x_values >= min_x) & (x_values <= max_x)] = f(x_values_interp)
        data.append(interpolate_and_restore_nans(y_values, 51))

    # Compute the final average of the aligned datasets
    average = np.nanmean(data, axis=0)

    # Save the average to a DataFrame
    average_df = pd.DataFrame({'X': x_values, 'Y': average})
    average_df = average_df.dropna(subset=['Y'])  # Remove rows where Y is NaN
    
    return average_df

# Define the common X values (logarithmically spaced from 20 Hz to 20 kHz)
x_values = np.logspace(np.log10(20), np.log10(20000), num=2000)

# Create a new DataFrame to store the IEM name, the average measurement, and the contributing reviewers
avg_df = pd.DataFrame(columns=['IEM', 'Average Measurement', 'Contributing Reviewers'])

# Loop through all IEMs and calculate the average measurement
for iem, row in iem_df.iterrows():
    data_frames = []
    contributing_reviewers = []
    
    for reviewer, files in row.items():
        if files:
            for file in files:
                file_path = os.path.join(f'output/csv/{reviewer}', file)
                try:
                    df = pd.read_csv(file_path, delimiter='\t', header=None, names=['X', 'Y'])
                    df['X'] = pd.to_numeric(df['X'], errors='coerce')
                    df['Y'] = pd.to_numeric(df['Y'], errors='coerce')
                    df = df.dropna()
                    if not df.empty:
                        data_frames.append(df)
                        contributing_reviewers.append(reviewer)
                except Exception as e:
                    print(f"Skipping file {file_path} due to an error: {e}")


    
    average_measurement = calculate_average(data_frames, x_values)
    avg_df = avg_df.append({'IEM': iem, 'Average Measurement': average_measurement, 'Contributing Reviewers': contributing_reviewers}, ignore_index=True)

print(avg_df)


C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:31: RuntimeWarning: Mean of empty slice
  average = np.nanmean(data, axis=0)
C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:68: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({'IEM': iem, 'Average Measurement': average_measurement, 'Contributing Reviewers': contributing_reviewers}, ignore_index=True)
C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:31: RuntimeWarning: Mean of empty slice
  average = np.nanmean(data, axis=0)
C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:68: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({'IEM': iem, 'Average Measurement': average_measurement, 'Contributing Reviewers': contributing_reviewers}, ignore_index=True)
C:\Users\Agnes\AppDa

Skipping file output/csv/hbb\HBB 1 R.csv due to an error: Error tokenizing data. C error: Expected 2 fields in line 7, saw 3



C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:31: RuntimeWarning: Mean of empty slice
  average = np.nanmean(data, axis=0)
C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:68: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({'IEM': iem, 'Average Measurement': average_measurement, 'Contributing Reviewers': contributing_reviewers}, ignore_index=True)
C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:31: RuntimeWarning: Mean of empty slice
  average = np.nanmean(data, axis=0)
C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\412343808.py:68: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({'IEM': iem, 'Average Measurement': average_measurement, 'Contributing Reviewers': contributing_reviewers}, ignore_index=True)
C:\Users\Agnes\AppDa

KeyboardInterrupt: 

In [29]:
avg_df

IEM  \
0                                       7Hz Dioko L.csv   
1                                     7Hz Eternal L.csv   
2                                      7Hz Legato L.csv   
3                                    7Hz Timeless L.csv   
4                                        7Hz Zero L.csv   
...                                                 ...   
2351                   710 Btnc (Active, ANC off) L.csv   
2352                          Elegia (Stock Pads) L.csv   
2353  Elex (Dekoni Elite Fenestrated Sheepskin Pads)...   
2354                                          Ola L.csv   
2355                                         test L.csv   

                            Average Measurement Contributing Reviewers  
0     Empty DataFrame
Columns: [X, Y]
Index: []                     []  
1     Empty DataFrame
Columns: [X, Y]
Index: []                     []  
2     Empty DataFrame
Columns: [X, Y]
Index: []                     []  
3     Empty DataFrame
Columns: [X, Y]
Index: []                     []  
4     Empty DataFrame
Columns: [X, Y]
Index: []                     []  
...                                         ...                    ...  
2351  Empty DataFrame
Columns: [X, Y]
Index: []                     []  
2352  Empty DataFrame
Columns: [X, Y]
Index: []                     []  
2353  Empty DataFrame
Columns: [X, Y]
Index: []                     []  
2354  Empty DataFrame
Columns: [X, Y]
Index: []                     []  
2355  Empty DataFrame
Columns: [X, Y]
Index: []                     []  

[2356 rows x 3 columns]

In [45]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy.interpolate import interp1d
from scipy.signal import savgol_filter

def read_and_interpolate(file_path, x_values):
    df = pd.read_csv(file_path)
    
    # Group data points by the same X-value and take the mean of their Y-values
    df = df.groupby('X', as_index=False).mean()
    
    min_x = df['X'].min()
    max_x = df['X'].max()
    x_values_interp = x_values[(x_values >= min_x) & (x_values <= max_x)]
    f = interp1d(df['X'], df['Y'], kind='linear', fill_value='extrapolate')
    y_values = np.empty_like(x_values)
    y_values[:] = np.nan
    y_values[(x_values >= min_x) & (x_values <= max_x)] = f(x_values_interp)
    return y_values

def generate_x_values():
    x_values = np.logspace(np.log10(20), np.log10(20000), num=1000)
    return np.concatenate(([0], x_values))

def calculate_average(file_paths, output_path):
    x_values = generate_x_values()

    # Read and interpolate all .csv files
    data = []
    for file_path in file_paths:
        try:
            interpolated_data = read_and_interpolate(file_path, x_values)
            # Create a DataFrame with the interpolated data
            interpolated_df = pd.DataFrame({'X': x_values, 'Y': interpolated_data})
            data.append(interpolated_df)
        except KeyError as e:
            print(f"KeyError in {file_path}: {e}. Skipping this file.")

    def find_mean_in_range(data, x_min, x_max):
        return np.mean([df.loc[(df['X'] >= x_min) & (df['X'] <= x_max), 'Y'] for df in data])

    average = []
    for x_min, x_max in zip(x_values[:-1], x_values[1:]):
        mean = find_mean_in_range(data, x_min, x_max)
        average.append(mean)

    # Save average to .csv
    df = pd.DataFrame({'X': x_values[:-1], 'Y': average})
    df.to_csv(output_path, index=False)

    return x_values, average, data


def calculate_iem_average(iem, reviewers_files, output_directory):
    print(f"Reviewers_files for {iem}:\n{reviewers_files}\n")  # Add this line for debugging
    
    file_paths = []
    for reviewer in reviewers_files.index:
        files = reviewers_files[reviewer]
        if files:
            for file in files:  # Add this loop to iterate over the file paths in each cell
                file_path = os.path.join(output_directory, '..', 'csv', reviewer, file).replace('\\', '/')
                file_paths.append(file_path)

    output_path = os.path.join(output_directory, f"Average_{iem}.csv")

    x_values, average, data = calculate_average(file_paths, output_path)
    return x_values, average, data


# Create a new DataFrame to store the average measurements
avg_df = pd.DataFrame(columns=['IEM', 'Average Measurement', 'Reviewers'])

# Calculate the average for each IEM
output_directory = 'output/averages'
os.makedirs(output_directory, exist_ok=True)

for iem, reviewers_files in iem_df.iterrows():
    x_values, average, data = calculate_iem_average(iem, reviewers_files, output_directory)

    avg_df = avg_df.append({
        'IEM': iem,
        'Average Measurement': average,
        'Reviewers': {reviewer: files for reviewer, files in reviewers_files.items() if files}
    }, ignore_index=True)

print(avg_df)


Reviewers_files for 7Hz Dioko L.csv:
achoreviews                                        [7Hz Dioko L.csv]
bedrock                           [7Hz Dioko L.csv, 7Hz Dioko R.csv]
timmyv                            [7Hz Dioko L.csv, 7Hz Dioko R.csv]
iemworld                          [7Hz Dioko L.csv, 7Hz Dioko R.csv]
data_mrs           [7Hz Dioko L.csv, 7Hz Dioko R.csv, 7Hz Dioko (...
aftersound         [7HZ SALNOTES DIOKO L.csv, 7HZ SALNOTES DIOKO ...
arn                                       [7Hz Salnotes Dioko L.csv]
pw                 [7Hz Salnotes Dioko L.csv, 7Hz Salnotes Dioko ...
hbb                                                [7Hz Dioko R.csv]
hobbytalk                         [7hz Dioko L.csv, 7hz Dioko R.csv]
ianfann            [7HZ DIOKO (bass mod) L.csv, 7HZ DIOKO (bass m...
kr0mka                                    [Dioko L.csv, Dioko R.csv]
kurin                        [Resolve 7Hz Salnotes Dioko Gras L.csv]
nymz               [7hz Salnotes Dioko L.csv, 7hz Salnotes Dioko .

C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\426194462.py:83: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({


Reviewers_files for 7Hz Eternal L.csv:
achoreviews                           [7Hz Eternal L.csv]
bedrock            [7Hz Eternal L.csv, 7Hz Eternal R.csv]
timmyv                                                 []
iemworld           [7Hz ETERNAL L.csv, 7Hz ETERNAL R.csv]
data_mrs                                               []
aftersound                                             []
arn                                                    []
pw                                                     []
hbb                                   [7Hz Eternal R.csv]
hobbytalk                                              []
ianfann                                                []
kr0mka                                                 []
kurin                                                  []
nymz                                                   []
vortexreviews      [7hz Eternal L.csv, 7hz Eternal R.csv]
vsg                [7Hz Eternal L.csv, 7Hz Eternal R.csv]
harpo                            

C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\426194462.py:83: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({


Reviewers_files for 7Hz Legato L.csv:
achoreviews                                       [7Hz Legato L.csv]
bedrock                                                           []
timmyv                          [7Hz Legato L.csv, 7Hz Legato R.csv]
iemworld                                                          []
data_mrs                                                          []
aftersound                      [7HZ LEGATO L.csv, 7HZ LEGATO R.csv]
arn                                                               []
pw                                                                []
hbb                                               [7Hz Legato R.csv]
hobbytalk                                                         []
ianfann                         [7HZ LEGATO L.csv, 7HZ LEGATO R.csv]
kr0mka                                                            []
kurin                                                             []
nymz                            [7hz LEGATO L.csv, 7hz LEGATO R.c

...

C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\426194462.py:83: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({


Reviewers_files for Ola L.csv:
achoreviews                       []
bedrock                           []
timmyv                            []
iemworld                          []
data_mrs                          []
aftersound                        []
arn                               []
pw                                []
hbb                               []
hobbytalk                         []
ianfann                           []
kr0mka                            []
kurin                             []
nymz                              []
vortexreviews                     []
vsg                               []
harpo                             []
cqtek                             []
rg                                []
soundjedi                         []
tgx78                             []
jacstone                          []
recode                            []
animagus                          []
bryaudioreviews                   []
cammyfi                           []
eplv   

C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\426194462.py:83: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({


Reviewers_files for test L.csv:
achoreviews                  []
bedrock                      []
timmyv                       []
iemworld                     []
data_mrs                     []
aftersound                   []
arn                          []
pw                           []
hbb                          []
hobbytalk                    []
ianfann                      []
kr0mka                       []
kurin                        []
nymz                         []
vortexreviews                []
vsg                          []
harpo                        []
cqtek                        []
rg                           []
soundjedi                    []
tgx78                        []
jacstone                     []
recode                       []
animagus                     []
bryaudioreviews              []
cammyfi                      []
eplv                         []
melatonin                    []
shortbus                     []
suporsalad                   []
wdym    

C:\Users\Agnes\AppData\Local\Temp\ipykernel_9224\426194462.py:83: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  avg_df = avg_df.append({


In [46]:
avg_df

IEM  \
0                                       7Hz Dioko L.csv   
1                                     7Hz Eternal L.csv   
2                                      7Hz Legato L.csv   
3                                    7Hz Timeless L.csv   
4                                        7Hz Zero L.csv   
...                                                 ...   
2351                   710 Btnc (Active, ANC off) L.csv   
2352                          Elegia (Stock Pads) L.csv   
2353  Elex (Dekoni Elite Fenestrated Sheepskin Pads)...   
2354                                          Ola L.csv   
2355                                         test L.csv   

                                    Average Measurement  \
0     [nan, nan, nan, nan, nan, nan, nan, nan, 89.77...   
1     [nan, nan, nan, nan, 89.54056836181194, 89.544...   
2     [nan, nan, nan, nan, 87.31758101470885, 87.315...   
3     [nan, nan, nan, nan, 80.79420928047142, 80.804...   
4     [nan, nan, nan, nan, nan, 85.88176984326728, 8...   
...                                                 ...   
2351  [nan, 73.6313962428586, 73.68771678009647, 73....   
2352  [nan, 78.97773430498528, 79.01533290539408, 79...   
2353  [nan, 70.53076126621039, 70.59249723972114, 70...   
2354  [nan, 74.6497282095405, 74.61305784740108, 74....   
2355  [nan, nan, nan, nan, 72.90216994177581, 72.918...   

                                              Reviewers  
0     {'achoreviews': ['7Hz Dioko L.csv'], 'bedrock'...  
1     {'achoreviews': ['7Hz Eternal L.csv'], 'bedroc...  
2     {'achoreviews': ['7Hz Legato L.csv'], 'timmyv'...  
3     {'achoreviews': ['7Hz Timeless L.csv'], 'timmy...  
4     {'achoreviews': ['7Hz Zero L.csv'], 'bedrock':...  
...                                                 ...  
2351  {'wdym': ['710 Btnc (Active, ANC off) L.csv', ...  
2352            {'wdym': ['Elegia (Stock Pads) L.csv']}  
2353  {'wdym': ['Elex (Dekoni Elite Fenestrated Shee...  
2354                     {'akros': ['Ola Stock L.csv']}  
2355                          {'akros': ['test L.csv']}  

[2356 rows x 3 columns]